In [7]:
# imports
import pandas as pd
import requests
import os
from pprint import pprint
import json


# Foursquare

Send a request to Foursquare with a small radius (1000m) for all the bike stations in your city of choice. 

In [8]:
#import list of lat long from city bikes notebook

%store -r cb_lat_long
api_key = os.environ["foursquare_api"]
radius = "1000" 

#ll = latitude and longitude   

headers = {
   "Accept": "application/json",
   'Authorization': api_key
   }

fields = "name,rating,popularity,price,distance,stats,location"
category = {"Dining and Drinking": "13000"}

fsq_responses = []
for latlong in cb_lat_long:
   ll = ",".join(map(str,latlong))
   url = "https://api.foursquare.com/v3/places/search?" + "&ll=" + ll + "&radius=" + radius + "&categories=" + category["Dining and Drinking"] + "&fields=" + fields
   result = requests.get(url, headers=headers)
   fsq_responses.append(result.json())  



In [10]:
#write to json file for later use
with open('fsq_responses.json', 'w') as f:
    json.dump(fsq_responses, f)
#a instead of w maybe

In [17]:
with open('fsq_responses.json') as fsq_json:
    fsq_data = json.load(fsq_json)
fsq_json.close()

In [ ]:
pprint(fsq_data)

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [57]:
fsq_list = []
for item in fsq_data:
    context = item['context']
    latitude = context['geo_bounds']['circle']['center']['latitude']
    longitude = context['geo_bounds']['circle']['center']['longitude']
    results = item['results']
    fsq_dict = {}
    fsq_dict['latitude'] = latitude
    fsq_dict['longitude'] = longitude
    for result in results:
        for key, value in result.items():
            fsq_dict[key] = value
    fsq_list.append(fsq_dict)
pprint(fsq_list)

[{'distance': 779,
  'latitude': 49.262487,
  'location': {'address': '28 5th Ave W',
               'country': 'CA',
               'cross_street': 'btwn Manitoba & Ontario',
               'formatted_address': '28 5th Ave W (btwn Manitoba & Ontario), '
                                    'Vancouver BC V5Y 1H5',
               'locality': 'Vancouver',
               'postcode': 'V5Y 1H5',
               'region': 'BC'},
  'longitude': -123.114397,
  'name': 'The Juice Truck',
  'popularity': 0.9125452812202097,
  'price': 1,
  'rating': 9.1,
  'stats': {'total_photos': 26, 'total_ratings': 38, 'total_tips': 3}},
 {'distance': 286,
  'latitude': 49.274566,
  'location': {'address': '1011 Mainland St',
               'country': 'CA',
               'cross_street': 'at Nelson St',
               'formatted_address': '1011 Mainland St (at Nelson St), '
                                    'Vancouver BC V6B 5P9',
               'locality': 'Vancouver',
               'postcode': 'V6B 5P9',


Put your parsed results into a DataFrame

In [58]:

foursquare_df = pd.DataFrame(fsq_list)
#foursquare_df.head()
address_df = pd.DataFrame.from_dict(foursquare_df.location.tolist())
stats_df = pd.DataFrame.from_dict(foursquare_df.stats.tolist())
foursquare_join_df = foursquare_df.join(address_df).join(stats_df)
foursquare_df_final = foursquare_join_df.drop(columns=['location', 'stats', 'address', 'country', 'cross_street', 'locality', 'postcode', 'address_extended', 'region',])
foursquare_df_final.head()


latitude   longitude  distance                                 name  \
0  49.262487 -123.114397       779                      The Juice Truck   
1  49.274566 -123.121817       286  The Keg Steakhouse + Bar - Yaletown   
2  49.279764 -123.110154       512                 Pourhouse Restaurant   
3  49.260599 -123.113504       618                        Rain or Shine   
4  49.264215 -123.117772       921                      The Juice Truck   

   popularity  price  rating  \
0    0.912545      1     9.1   
1    0.973651      3     8.2   
2    0.970276      2     9.0   
3    0.977197      1     8.6   
4    0.912545      1     9.1   

                                   formatted_address  total_photos  \
0  28 5th Ave W (btwn Manitoba & Ontario), Vancou...            26   
1  1011 Mainland St (at Nelson St), Vancouver BC ...           249   
2  162 Water St (btwn Cambie & Abbott), Vancouver...           343   
3    3382 Cambie St (18th Ave), Vancouver BC V5Z 2W5            95   
4  28 5th Ave W (btwn Manitoba & Ontario), Vancou...            26   

   total_ratings  total_tips  
0             38         3.0  
1            210        59.0  
2            380       118.0  
3             78        13.0  
4             38         3.0

# Yelp

Send a request to Yelp with a small radius (1000m) for all the bike stations in your city of choice. 

In [11]:
%store -r cb_lat_long
yelp_key = os.environ["yelp_api"]
yelp_radius = '1000'
yelp_headers = {
    "Accept": "application/json",
   'Authorization': 'Bearer ' + yelp_key
}

category_term = "dining and drinking"

yelp_responses = []
for latlong in cb_lat_long:
    latitude = str(latlong[0])
    longitude = str(latlong[1])
    url = 'https://api.yelp.com/v3/businesses/search?latitude=' + latitude + '&longitude=' + longitude + '&term=' + category_term + '&radius=' + yelp_radius + '&categories=' + category_term + '&sort_by=best_match'
    yelp_response = requests.get(url, headers=yelp_headers)
    if yelp_response.status_code == 200:
        yelp_responses.append(yelp_response.json())
    elif yelp_response.status_code == 429:
        print("Rate Limited")
    elif yelp_response.status_code == 400:
        print("Invalid Request")
    else:
        print("Other error. Investigate")

Other error. Investigate
Other error. Investigate


In [14]:
print(len(yelp_responses))
pprint(yelp_responses)

242
[{'businesses': [{'alias': 'la-taqueria-pinche-taco-shop-vancouver',
                  'categories': [{'alias': 'mexican', 'title': 'Mexican'}],
                  'coordinates': {'latitude': 49.263559,
                                  'longitude': -123.112736},
                  'display_phone': '+1 604-558-2549',
                  'distance': 169.51745604912014,
                  'id': '6iOAgzJ0DRZNSKA3FSrrOg',
                  'image_url': 'https://s3-media1.fl.yelpcdn.com/bphoto/fjhIj3XKuQ4mquD4Mg8OoQ/o.jpg',
                  'is_closed': False,
                  'location': {'address1': '2450 Yukon Street',
                               'address2': '',
                               'address3': '',
                               'city': 'Vancouver',
                               'country': 'CA',
                               'display_address': ['2450 Yukon Street',
                                                   'Vancouver, BC V5Z 3V6',
                                

In [46]:
#write to json file for later use
with open('yelp_responses.json', 'w') as f:
    json.dump(yelp_responses, f)

In [51]:
with open('yelp_responses.json') as yelp_json:
    yelp_data = json.load(yelp_json)

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [59]:
yelp_list = []
key_list = ['coordinates', 'name', 'distance', 'price', 'rating', 'location']
for item in yelp_data:
    for business in item['businesses']:
        business_dict = {}
        business_dict['latitude'] = business['coordinates']['latitude']
        business_dict['longitude'] = business['coordinates']['longitude']
        business_dict['address'] = business['location']['display_address']
        for key, value in business.items():
            business_dict[key] = value
    yelp_list.append(business_dict)
pprint(yelp_list)

[{'address': ['601 Stamps Landing',
              'Unit 36',
              'Vancouver, BC V5Z 3Z1',
              'Canada'],
  'alias': 'mahony-s-tavern-vancouver',
  'categories': [{'alias': 'irish_pubs', 'title': 'Irish Pub'}],
  'coordinates': {'latitude': 49.268991869566904,
                  'longitude': -123.11856069065676},
  'display_phone': '+1 604-876-0234',
  'distance': 783.8684935220706,
  'id': 'g1WcsMOzDGOmDvA-y0xMvQ',
  'image_url': 'https://s3-media3.fl.yelpcdn.com/bphoto/ymBvc65fIE-ANl6PHfQCTA/o.jpg',
  'is_closed': False,
  'latitude': 49.268991869566904,
  'location': {'address1': '601 Stamps Landing',
               'address2': 'Unit 36',
               'address3': '',
               'city': 'Vancouver',
               'country': 'CA',
               'display_address': ['601 Stamps Landing',
                                   'Unit 36',
                                   'Vancouver, BC V5Z 3Z1',
                                   'Canada'],
               'state': 

Put your parsed results into a DataFrame

In [74]:
yelp_raw_df = pd.DataFrame(yelp_list)
#columns to drop = address, id, alias, image_url, is_closed, url, categproes, transactions, location, phone, display_phone, address3, city, zip_code, country, state, display_address
yelp_address_df = pd.DataFrame.from_dict(yelp_raw_df.location.tolist())
yelp_join_df = yelp_raw_df.join(yelp_address_df)
yelp_df_final = yelp_join_df.drop(columns=['address', 'id', 'alias', 'image_url', 'is_closed', 'url', 'coordinates', 'categories', 'transactions', 'location', 'phone', 'display_phone', 'address3', 'city', 'zip_code', 'country', 'state', 'display_address'])
yelp_df_final.head()

latitude   longitude                       name  review_count  rating  \
0  49.268992 -123.118561            Mahony’s Tavern           163     2.5   
1  49.277706 -123.114148  District Bar & Restaurant            93     4.0   
2  49.285541 -123.118816           Cactus Club Cafe           479     4.0   
3  49.266368 -123.104530              Tacofino Ocho            86     3.0   
4  49.258843 -123.114166                 V Yaletown             6     3.5   

  price    distance              address1     address2  
0    $$  783.868494    601 Stamps Landing      Unit 36  
1    $$  656.787425     121 Robson Street               
2    $$  898.561850    588 Burrard Street               
3    $$  914.072331        8 East 5th Ave               
4    $$  652.165471  1095 Mainland Street  Upper Level

# Comparing Results

Which API provided you with more complete data? Provide an explanation. 

Get the top 10 restaurants according to their rating